# Accessing ERDDAP data with R
[![R Binder Badge](https://img.shields.io/badge/Launch-R_Binder-blue)](https://mybinder.org/v2/gh/NOAA-CEFI-Portal/cefi-cookbook/r-setup?urlpath=git-pull%3Frepo%3Dhttps%253A%252F%252Fgithub.com%252FNOAA-CEFI-Portal%252Fcefi-cookbook%26urlpath%3Dlab%252Ftree%252Fcefi-cookbook%252Fcontent%252Fdata_access%252Faccess_erddap%252FR_erddap.ipynb%26branch%3Dmain)

The following notebook is a quick demostration on how to use R to access the ERDDAP server data. This is designed for users that prefer the programing interface to be R. There are already couple of great resource related to preprocessing and visualizing data in R. Therefore, the notebook will not repeat that part of the code but focusing on how to accessing the data from a R interface. The resources is listed below 
> - http://cran.nexr.com/web/packages/rerddap/vignettes/Using_rerddap.html (A detail introduction of rerddap package and show the visualization in many different datasets)
> - https://ioos.github.io/ioos_code_lab/content/code_gallery/data_access_notebooks/2017-08-01-xtractoR.html (use a different package called xtractomatic to access the ERDDAP data)

<div class="admonition alert alert-info">
    <p class="admonition-title" style="font-weight:bold">Launch R in Jupyterlab</p>
    In addition to the standard R code demonstrated below, our current interface leverages JupyterLab to execute R code using the R kernel. To enable this functionality, we utilize the environment.yml file to create a Conda/Mamba environment. The primary objective is to install the r-irkernel package within this environment.

This installation of r-irkernel through Conda/Mamba ensures that the R kernel becomes available as an option when launching JupyterLab. Selecting the R kernel empowers users to utilize the JupyterLab interface for running R code effortlessly.
    
</div>

## Packages used
To use R to access the ERDDAP server directly from your R script or R-notebook, you will need
- rerddap

There are couple of ways to install the `rerddap` package, here we provide two popular ways below
1. In the R environment, `install.packages('rerddap')`
2. In the conda environment for different package version control, `conda install r-rerddap` (many r package can be install this way by adding "r-" in front of the package name)


## Import R packages
The way to import packages to the current R environment is to use the `require` or `library` functions
Both functions will import the package but with subtle different of 
> The require() and library() functions can both be used to load packages in R, but they have one subtle difference:
>
> - require() will output a warning if a package is not installed and then continue to execute the code.
> - library() will output an error and stop the execution of the code.

Detail explanation cna be find [here](https://www.statology.org/r-require-vs-library/#:~:text=The%20require()%20and%20library,the%20execution%20of%20the%20code.)

In [1]:
library("rerddap")

## Help page for the package and related functions
A great way to find information about the package directly in the R-notebook environment is to add the `?` in front of the package/function name

In [2]:
?rerddap

rerddap-package            package:rerddap             R Documentation

_r_e_r_d_d_a_p

_D_e_s_c_r_i_p_t_i_o_n:

     General purpose R client for ERDDAP servers

_E_R_D_D_A_P _i_n_f_o:

     NOAA's ERDDAP service holds many datasets of interest. It's built
     on top of OPenDAP. You can search for datasets via ‘ed_search()’,
     list datasets via ‘ed_datasets()’, get information on a single
     dataset via ‘info()’, then get data you want for either tabledap
     type via ‘tabledap()’, or for griddap type via ‘griddap()’

_t_a_b_l_e_d_a_p/_g_r_i_d_d_a_p:

     tabledap and griddap have different interfaces to query for data,
     so ‘tabledap()’ and ‘griddap()’ are separated out as separate
     functions even though some of the internals are the same. In
     particular, with tabledap you can query on/subset all variables,
     whereas with gridddap, you can only query on/subset the dimension
     varibles (e.g., latitude, longitude, altitude).

_D_a_t_a _s_i_z_e:

     With griddap data via ‘griddap()’ you can get a lot of data
     quickly. Try small searches of a dataset to start to get a sense
     for the data, then you can increase the amount of data you get.
     See ‘griddap()’ for more details.

_C_a_c_h_i_n_g:

     ‘rerddap’ by default caches the requests you make, so that if you
     happen to make the same request again, the data is restored from
     the cache, rather than having to go out and retrieve it remotely.
     For most applications, this is good, as it can speed things up
     when doing a lot of request in a script, and works because in most
     cases an ERDDAP request is "idempotent".  This means that the the
     request will always return the same thing no matter what requests
     came before - it doesn't depend on state. However this is not true
     if the script uses either "last" in ‘griddap()’ or "now" in
     ‘tabledap()’ as these will return different values as time elapses
     and data are added to the datasets.  While it is desirable to have
     ERDDAP purely idempotent, the "last" and "now" constructs are very
     helpful for people using ERDDAP in dashboards, webpages, regular
     input to models and the like, and the benefits far outweigh the
     problems.  However, if you are using either "last" or "now" in an
     ‘rerddap’ based script, you want to be very careful to clear the
     ‘rerddap’ cache, otherwise the request will be viewed as the same,
     and the data from the last request, rather than the latest data,
     will be returned.

To find information about a function in a specific package

In [3]:
?rerddap::ed_search

ed_search               package:rerddap                R Documentation

_S_e_a_r_c_h _f_o_r _E_R_D_D_A_P _t_a_b_l_e_d_e_p _o_r _g_r_i_d_d_a_p _d_a_t_a_s_e_t_s

_D_e_s_c_r_i_p_t_i_o_n:

     Search for ERDDAP tabledep or griddap datasets

_U_s_a_g_e:

     ed_search(
       query,
       page = NULL,
       page_size = NULL,
       which = "griddap",
       url = eurl(),
       ...
     )
     
     ed_datasets(which = "tabledap", url = eurl())
     
_A_r_g_u_m_e_n_t_s:

   query: (character) Search terms

    page: (integer) Page number

page_size: (integer) Results per page

   which: (character) One of tabledep or griddap.

     url: A URL for an ERDDAP server. Default:
          https://upwell.pfeg.noaa.gov/erddap/ - See ‘eurl()’ for more
          information

     ...: Curl options passed on to crul::verb-GET (must be named
          parameters)

_R_e_f_e_r_e_n_c_e_s:

     https://upwell.pfeg.noaa.gov/erddap/index.html

_E_x_a_m_p_l_e_s:

     ## Not run:
     
     (out <- ed_search(query='temperature'))
     out$alldata[[1]]
     (out <- ed_search(query='size'))
     out$info
     
     # List datasets
     ed_datasets('table')
     ed_datasets('grid')
     
     # use a different ERDDAP server
     ## Marine Institute (Ireland)
     ed_search("temperature", url = "http://erddap.marine.ie/erddap/")
     ## End(Not run)

## Direct ERDDAP server based search of datasets

The `rerddap::ed_search` helps user search for data directly on a ERDDAP server. It give user an output of all dataset full names and the associated dataset_id which is important for the downloading. Here we demostrate the `ed_search` function with query of sea surface temperature (sst) dataset.

In [4]:
whichSST <- rerddap::ed_search(query = "sst")

In [5]:
whichSST

# A tibble: 980 × 2
   title                                                              dataset_id
   <chr>                                                              <chr>     
 1 COBE SST Analysis (sst.mon.ltm.1981-2010), 1.0°, 0001              noaa_psl_…
 2 COBE SST Analysis (sst.mon.ltm.1991-2020), 1.0°, 0001              noaa_psl_…
 3 COBE SST Analysis (sst.mon.mean), 1.0°, 1891-present               noaa_psl_…
 4 HadISST Average Sea Surface Temperature, 1°, Global, Monthly, 187… erdHadISST
 5 HadISST Average Sea Surface Temperature, 1°, Global, Monthly, 187… erdHadISS…
 6 NOAA ERSSTv4 (in situ only), 2°, Global, Monthly, 1854-2020        nceiErsst…
 7 NOAA ERSSTv4 (in situ only), 2°, Global, Monthly, 1854-2020, Lon+… nceiErsst…
 8 NOAA ERSSTv5 (in situ only) (sst.mnmean), 2.0°, 1854-present       noaa_psl_…
 9 NOAA ERSSTv5 (in situ only) (sst.mon.ltm), 2.0°, 0001              noaa_psl_…
10 NOAA ERSSTv5 (in situ only) (sst.mon.ltm.1981-2010), 2.0°, 0001    noaa_psl_…
# ℹ 970 

If the url argument is not specified, the search will be the default ERDDAP server which is located at [ NOAA NMFS SWFSC ERD](https://coastwatch.pfeg.noaa.gov/erddap/index.html). To switch from the default server to a specific server, one can set the server url manually in one of the argument as the following.

In [7]:
whichSST2 <- rerddap::ed_search(query = "sst", url = "https://erddap.ifremer.fr/erddap/")

Once the url is changed to other server, a different set of SST dataset can been seen below.

In [8]:
whichSST2

# A tibble: 2 × 2
  title                        dataset_id                    
  <chr>                        <chr>                         
1 Daily MUR SST, Final product SST_Anomalies_Caledonie       
2 Global Odyssea SST Analysis  IFR-L4-SSTfnd-ODYSSEA-GLOB_010

## Information about the dataset
For a quick peek of the data meta data, one can also use the `info` function 

In [11]:
info('SST_Anomalies_Caledonie',url = "https://erddap.ifremer.fr/erddap/")

<ERDDAP info> SST_Anomalies_Caledonie 
 Base URL: https://erddap.ifremer.fr/erddap 
 Dataset Type: griddap 
 Dimensions (range):  
     time: (2014-01-16T09:00:00Z, 2021-12-16T09:00:00Z) 
     latitude: (-27.0, -14.01) 
     longitude: (155.01, 175.01) 
 Variables:  
     analysed_sst: 
         Units: kelvin 

## Subsetting and download to local memory
Here we focus on downloading a gridded dataset in the default ERDDAP server and subsetting it in the notebook.

In [12]:
sstInfo <- info('nceiErsstv5_LonPM180')
erSST <- griddap(sstInfo, latitude = c(22., 51.), longitude = c(-140., -105), time = c("2017-01-01", "2017-01-02"), fields = 'ssta')

info() output passed to x; setting base url to: https://upwell.pfeg.noaa.gov/erddap



erSST

The data can be viewed or used in the form of a data frame in R as following

In [8]:
erSST$data

longitude latitude depth time                 ssta     
1   -140      22       0     2017-01-15T00:00:00Z 0.4975815
2   -138      22       0     2017-01-15T00:00:00Z 0.5484982
3   -136      22       0     2017-01-15T00:00:00Z 0.6286888
4   -134      22       0     2017-01-15T00:00:00Z 0.6980591
5   -132      22       0     2017-01-15T00:00:00Z 0.7338963
6   -130      22       0     2017-01-15T00:00:00Z 0.7631321
7   -128      22       0     2017-01-15T00:00:00Z 0.8205128
8   -126      22       0     2017-01-15T00:00:00Z 0.8727989
9   -124      22       0     2017-01-15T00:00:00Z 0.8595047
10  -122      22       0     2017-01-15T00:00:00Z 0.7678528
11  -120      22       0     2017-01-15T00:00:00Z 0.6379509
12  -118      22       0     2017-01-15T00:00:00Z 0.5156460
13  -116      22       0     2017-01-15T00:00:00Z 0.3866863
14  -114      22       0     2017-01-15T00:00:00Z 0.3033581
15  -112      22       0     2017-01-15T00:00:00Z 0.2495575
16  -110      22       0     2017-01-15T00:00:00Z 0.2187004
17  -108      22       0     2017-01-15T00:00:00Z 0.2276649
18  -106      22       0     2017-01-15T00:00:00Z 0.2507744
19  -104      22       0     2017-01-15T00:00:00Z       NaN
20  -140      24       0     2017-01-15T00:00:00Z 0.5302029
21  -138      24       0     2017-01-15T00:00:00Z 0.5568810
22  -136      24       0     2017-01-15T00:00:00Z 0.5974770
23  -134      24       0     2017-01-15T00:00:00Z 0.6192532
24  -132      24       0     2017-01-15T00:00:00Z 0.6023712
25  -130      24       0     2017-01-15T00:00:00Z 0.5866547
26  -128      24       0     2017-01-15T00:00:00Z 0.6152802
27  -126      24       0     2017-01-15T00:00:00Z 0.6616249
28  -124      24       0     2017-01-15T00:00:00Z 0.6624088
29  -122      24       0     2017-01-15T00:00:00Z 0.6034908
30  -120      24       0     2017-01-15T00:00:00Z 0.5108833
⋮   ⋮         ⋮        ⋮     ⋮                    ⋮        
275 -124      50       0     2017-01-15T00:00:00Z 0.3266554
276 -122      50       0     2017-01-15T00:00:00Z       NaN
277 -120      50       0     2017-01-15T00:00:00Z       NaN
278 -118      50       0     2017-01-15T00:00:00Z       NaN
279 -116      50       0     2017-01-15T00:00:00Z       NaN
280 -114      50       0     2017-01-15T00:00:00Z       NaN
281 -112      50       0     2017-01-15T00:00:00Z       NaN
282 -110      50       0     2017-01-15T00:00:00Z       NaN
283 -108      50       0     2017-01-15T00:00:00Z       NaN
284 -106      50       0     2017-01-15T00:00:00Z       NaN
285 -104      50       0     2017-01-15T00:00:00Z       NaN
286 -140      52       0     2017-01-15T00:00:00Z 0.1538076
287 -138      52       0     2017-01-15T00:00:00Z 0.1613760
288 -136      52       0     2017-01-15T00:00:00Z 0.1883817
289 -134      52       0     2017-01-15T00:00:00Z 0.2515111
290 -132      52       0     2017-01-15T00:00:00Z 0.3357005
291 -130      52       0     2017-01-15T00:00:00Z 0.3924646
292 -128      52       0     2017-01-15T00:00:00Z 0.4165292
293 -126      52       0     2017-01-15T00:00:00Z       NaN
294 -124      52       0     2017-01-15T00:00:00Z       NaN
295 -122      52       0     2017-01-15T00:00:00Z       NaN
296 -120      52       0     2017-01-15T00:00:00Z       NaN
297 -118      52       0     2017-01-15T00:00:00Z       NaN
298 -116      52       0     2017-01-15T00:00:00Z       NaN
299 -114      52       0     2017-01-15T00:00:00Z       NaN
300 -112      52       0     2017-01-15T00:00:00Z       NaN
301 -110      52       0     2017-01-15T00:00:00Z       NaN
302 -108      52       0     2017-01-15T00:00:00Z       NaN
303 -106      52       0     2017-01-15T00:00:00Z       NaN
304 -104      52       0     2017-01-15T00:00:00Z       NaN

## Getting all dataset information in a ERDDAP server

The following steps show the way of listing out all dataset that is available in a ERDDAP using the tabledap function. 

In [14]:
urlBase <- "https://gliders.ioos.us/erddap/"
dataInfo <- rerddap::info("allDatasets", url = urlBase)

In [15]:
allGlider <- tabledap(dataInfo)

info() output passed to x; setting base url to: https://gliders.ioos.us/erddap



In [16]:
allGlider[0:10,0:3]

datasetID                    accessible
2  allDatasets                  public    
3  amelia-20180501T0000         public    
4  amelia-20200825T1929         public    
5  amelia-20201015T1436         public    
6  amlr01-20181216T0641-delayed public    
7  amlr01-20191206T0452-delayed public    
8  amlr02-20181211T1233-delayed public    
9  amlr02-20191206T1236-delayed public    
10 amlr03-20191206T0529-delayed public    
11 angus-20190522T0000          public    
   institution                                          
2  IOOS Glider DAC                                      
3  Virginia Institute of Marine Science - William & Mary
4  Virginia Institute of Marine Science - William & Mary
5  Virginia Institute of Marine Science - William & Mary
6  NOAA SWFSC Antarctic Ecosystem Research Division     
7  NOAA SWFSC Antarctic Ecosystem Research Division     
8  NOAA SWFSC Antarctic Ecosystem Research Division     
9  NOAA SWFSC Antarctic Ecosystem Research Division     
10 NOAA SWFSC Antarctic Ecosystem Research Division     
11 Skidaway Institute of Oceanography